In [18]:
from tensorflow.keras import backend as K
from tensorflow.keras.layers import Dense, Activation, Input
from tensorflow.keras.models import Model, load_model
from tensorflow.keras.optimizers import Adam
import numpy as np
import gym
import tensorflow as tf

In [28]:


class Agent(object):
    def __init__(self, alpha=0.01, gamma=0.99, n_actions=2,
                 layer1_size=256, layer2_size=128, input_dims=4):
        self.gamma = gamma
        self.alpha = alpha
        self.eps = np.finfo(np.float32).eps.item()
        self.input_dims = input_dims
        self.fc1_dims = layer1_size
        self.fc2_dims = layer2_size
        self.n_actions = n_actions
        
        self.rewards_history = []
        self.action_probs_history = []
        self.critic_value_history = []
        self.optimizer= tf.keras.optimizers.Adam(learning_rate=0.01)

        self.actor_critic = self.build_actor_critic_network()
        self.action_space = [i for i in range(n_actions)]

    def build_actor_critic_network(self):
        inputs = Input(shape=(self.input_dims,))
        delta = Input(shape=[1])
        dense1 = Dense(self.fc1_dims, activation='relu')(inputs)
        dense2 = Dense(self.fc2_dims, activation='relu')(dense1)
        probs = Dense(self.n_actions, activation='softmax')(dense2)
        values = Dense(1, activation='linear')(dense2)
        
        model = tf.keras.Model(inputs=inputs, outputs=[probs, values])

        return model

    def choose_action(self, action_probs):
        action = np.random.choice(agent.n_actions, p=np.squeeze(action_probs))

        return action
    def mem(self,reward,action_probs,critic_value):
        self.rewards_history.append(reward)
        self.action_probs_history.append(action_probs)
        self.critic_value_history.append(critic_value)
        
    def learn(self, ):
        huber_loss = keras.losses.Huber()
        with tf.GradientTape() as tape:
            returns = []
            discounted_sum = 0
            for r in self.rewards_history[::-1]:
                discounted_sum = r + gamma * discounted_sum
                returns.insert(0, discounted_sum)
            
            returns = np.array(returns)
            returns = (returns - np.mean(returns)) / (np.std(returns) + self.eps)
            returns = returns.tolist()
            
            # Calculating loss values to update our network
            history = zip(self.action_probs_history, self.critic_value_history, returns)
            actor_losses = []
            critic_losses = []
            for log_prob, value, ret in history:
                # At this point in history, the critic estimated that we would get a
                # total reward = `value` in the future. We took an action with log probability
                # of `log_prob` and ended up recieving a total reward = `ret`.
                # The actor must be updated so that it predicts an action that leads to
                # high rewards (compared to critic's estimate) with high probability.
                diff = ret - value
                actor_losses.append(-log_prob * diff)  # actor loss

                # The critic must be updated so that it predicts a better estimate of
                # the future rewards.
                critic_losses.append(huber_loss(tf.expand_dims(value, 0), tf.expand_dims(ret, 0)))
                # Backpropagation
            loss_value = sum(actor_losses) + sum(critic_losses)
            grads = tape.gradient(loss_value, self.actor_critic.trainable_variables)
            self.optimizer.apply_gradients(zip(grads, self.actor_critic.trainable_variables))

            # Clear the loss and reward history
            self.action_probs_history.clear()
            self.critic_value_history.clear()
            self.rewards_history.clear()



In [29]:

action_probs_history = []
critic_value_history = []
rewards_history = []
running_reward = 0
episode_count = 0
# Configuration parameters for the whole setup
seed = 42
gamma = 0.99  # Discount factor for past rewards
max_steps_per_episode = 10000
env = gym.make("CartPole-v0")  # Create the environment
env.seed(seed)
agent=Agent()
while True:  # Run until solved
    state = env.reset()
    episode_reward = 0
  
    for timestep in range(1, max_steps_per_episode):

        state = tf.convert_to_tensor(state)
        state = tf.expand_dims(state, 0)

        action_probs, critic_value = agent.actor_critic(state)
        # Sample action from action probability distribution
        action = agent.choose_action(action_probs)
        # Apply the sampled action in our environment
        state, reward, done, _ = env.step(action)
        episode_reward += reward
        agent.mem(reward,tf.math.log(action_probs[0, action]),critic_value[0, 0])

        if done:
            break

    # Update running reward to check condition for solving
    running_reward = 0.05 * episode_reward + (1 - 0.05) * running_reward

        
    # Log details
    episode_count += 1
    if episode_count % 10 == 0:
        template = "running reward: {:.2f} at episode {}"
        print(template.format(running_reward, episode_count))

    if running_reward > 195:  # Condition to consider the task solved
        print("Solved at episode {}!".format(episode_count))
        break

running reward: 8.09 at episode 10
running reward: 14.77 at episode 20
running reward: 16.12 at episode 30
running reward: 18.22 at episode 40
running reward: 18.41 at episode 50
running reward: 20.15 at episode 60
running reward: 21.85 at episode 70
running reward: 25.07 at episode 80
running reward: 21.54 at episode 90
running reward: 21.83 at episode 100
running reward: 20.30 at episode 110
running reward: 20.76 at episode 120
running reward: 20.00 at episode 130
running reward: 21.74 at episode 140
running reward: 21.06 at episode 150
running reward: 23.82 at episode 160
running reward: 21.98 at episode 170
running reward: 23.42 at episode 180
running reward: 21.51 at episode 190
running reward: 20.03 at episode 200
running reward: 20.01 at episode 210
running reward: 19.64 at episode 220
running reward: 20.89 at episode 230
running reward: 20.60 at episode 240
running reward: 21.18 at episode 250
running reward: 19.75 at episode 260
running reward: 20.84 at episode 270
running rew

running reward: 19.53 at episode 2200
running reward: 20.04 at episode 2210
running reward: 22.23 at episode 2220
running reward: 21.75 at episode 2230
running reward: 20.12 at episode 2240
running reward: 21.12 at episode 2250
running reward: 22.65 at episode 2260
running reward: 23.93 at episode 2270
running reward: 20.86 at episode 2280
running reward: 24.74 at episode 2290
running reward: 23.92 at episode 2300
running reward: 22.08 at episode 2310
running reward: 19.62 at episode 2320
running reward: 19.72 at episode 2330
running reward: 20.08 at episode 2340
running reward: 22.01 at episode 2350
running reward: 20.69 at episode 2360
running reward: 20.98 at episode 2370
running reward: 22.08 at episode 2380
running reward: 22.26 at episode 2390
running reward: 22.70 at episode 2400
running reward: 25.22 at episode 2410
running reward: 23.02 at episode 2420
running reward: 20.65 at episode 2430
running reward: 19.17 at episode 2440
running reward: 19.46 at episode 2450
running rewa

running reward: 20.62 at episode 4360
running reward: 21.08 at episode 4370
running reward: 22.05 at episode 4380
running reward: 23.37 at episode 4390
running reward: 22.29 at episode 4400
running reward: 20.42 at episode 4410
running reward: 21.34 at episode 4420
running reward: 21.34 at episode 4430
running reward: 19.75 at episode 4440
running reward: 18.42 at episode 4450
running reward: 19.04 at episode 4460
running reward: 18.24 at episode 4470
running reward: 18.67 at episode 4480
running reward: 20.25 at episode 4490
running reward: 19.40 at episode 4500
running reward: 19.93 at episode 4510
running reward: 19.14 at episode 4520
running reward: 19.00 at episode 4530
running reward: 19.86 at episode 4540
running reward: 18.85 at episode 4550
running reward: 19.83 at episode 4560
running reward: 19.78 at episode 4570
running reward: 18.49 at episode 4580
running reward: 20.47 at episode 4590
running reward: 18.83 at episode 4600
running reward: 16.90 at episode 4610
running rewa

running reward: 22.33 at episode 6520
running reward: 22.84 at episode 6530
running reward: 20.64 at episode 6540
running reward: 19.06 at episode 6550
running reward: 19.93 at episode 6560
running reward: 20.75 at episode 6570
running reward: 21.55 at episode 6580
running reward: 21.86 at episode 6590
running reward: 18.49 at episode 6600
running reward: 19.17 at episode 6610
running reward: 18.62 at episode 6620
running reward: 20.42 at episode 6630
running reward: 21.29 at episode 6640
running reward: 23.24 at episode 6650
running reward: 23.59 at episode 6660
running reward: 21.02 at episode 6670
running reward: 21.73 at episode 6680
running reward: 24.99 at episode 6690
running reward: 22.86 at episode 6700
running reward: 24.77 at episode 6710
running reward: 24.24 at episode 6720
running reward: 21.40 at episode 6730
running reward: 20.13 at episode 6740
running reward: 22.18 at episode 6750
running reward: 22.15 at episode 6760
running reward: 22.50 at episode 6770
running rewa

running reward: 20.05 at episode 8680
running reward: 21.00 at episode 8690
running reward: 19.66 at episode 8700
running reward: 20.38 at episode 8710
running reward: 19.43 at episode 8720
running reward: 19.09 at episode 8730
running reward: 19.49 at episode 8740
running reward: 19.86 at episode 8750
running reward: 21.73 at episode 8760
running reward: 21.45 at episode 8770
running reward: 20.97 at episode 8780
running reward: 18.94 at episode 8790
running reward: 20.73 at episode 8800
running reward: 21.12 at episode 8810
running reward: 23.53 at episode 8820
running reward: 23.42 at episode 8830
running reward: 24.17 at episode 8840
running reward: 23.52 at episode 8850
running reward: 20.43 at episode 8860
running reward: 19.94 at episode 8870
running reward: 20.68 at episode 8880
running reward: 22.26 at episode 8890
running reward: 22.29 at episode 8900
running reward: 24.66 at episode 8910
running reward: 24.94 at episode 8920
running reward: 24.30 at episode 8930
running rewa

...

running reward: 20.14 at episode 882560
running reward: 22.73 at episode 882570
running reward: 22.83 at episode 882580
running reward: 21.40 at episode 882590
running reward: 20.69 at episode 882600
running reward: 21.53 at episode 882610
running reward: 23.77 at episode 882620
running reward: 22.93 at episode 882630
running reward: 21.73 at episode 882640
running reward: 20.43 at episode 882650
running reward: 19.15 at episode 882660
running reward: 20.67 at episode 882670
running reward: 20.00 at episode 882680
running reward: 18.24 at episode 882690
running reward: 17.28 at episode 882700
running reward: 18.74 at episode 882710
running reward: 19.23 at episode 882720
running reward: 20.01 at episode 882730
running reward: 21.87 at episode 882740
running reward: 22.79 at episode 882750
running reward: 23.29 at episode 882760
running reward: 20.22 at episode 882770
running reward: 20.65 at episode 882780
running reward: 20.48 at episode 882790
running reward: 23.62 at episode 882800


running reward: 19.03 at episode 884610
running reward: 19.23 at episode 884620
running reward: 20.10 at episode 884630
running reward: 22.13 at episode 884640
running reward: 22.99 at episode 884650
running reward: 21.54 at episode 884660
running reward: 23.21 at episode 884670
running reward: 22.57 at episode 884680
running reward: 23.96 at episode 884690
running reward: 22.62 at episode 884700
running reward: 20.48 at episode 884710
running reward: 21.03 at episode 884720
running reward: 21.13 at episode 884730
running reward: 22.20 at episode 884740
running reward: 21.09 at episode 884750
running reward: 21.92 at episode 884760
running reward: 20.52 at episode 884770
running reward: 21.88 at episode 884780
running reward: 22.20 at episode 884790
running reward: 21.09 at episode 884800
running reward: 20.16 at episode 884810
running reward: 21.81 at episode 884820
running reward: 22.81 at episode 884830
running reward: 20.75 at episode 884840
running reward: 22.16 at episode 884850


running reward: 24.05 at episode 886660
running reward: 21.49 at episode 886670
running reward: 20.38 at episode 886680
running reward: 20.87 at episode 886690
running reward: 22.17 at episode 886700
running reward: 23.41 at episode 886710
running reward: 21.13 at episode 886720
running reward: 22.49 at episode 886730
running reward: 19.84 at episode 886740
running reward: 19.48 at episode 886750
running reward: 19.74 at episode 886760
running reward: 22.23 at episode 886770
running reward: 19.55 at episode 886780
running reward: 17.79 at episode 886790
running reward: 18.72 at episode 886800
running reward: 20.86 at episode 886810
running reward: 20.13 at episode 886820
running reward: 20.55 at episode 886830
running reward: 21.15 at episode 886840
running reward: 20.39 at episode 886850
running reward: 21.23 at episode 886860
running reward: 20.59 at episode 886870
running reward: 20.15 at episode 886880
running reward: 27.39 at episode 886890
running reward: 23.22 at episode 886900


running reward: 18.77 at episode 888710
running reward: 19.23 at episode 888720
running reward: 20.31 at episode 888730
running reward: 18.39 at episode 888740
running reward: 17.34 at episode 888750
running reward: 21.20 at episode 888760
running reward: 18.90 at episode 888770
running reward: 19.42 at episode 888780
running reward: 18.96 at episode 888790
running reward: 19.83 at episode 888800
running reward: 21.42 at episode 888810
running reward: 20.34 at episode 888820
running reward: 21.72 at episode 888830
running reward: 20.28 at episode 888840
running reward: 19.86 at episode 888850
running reward: 20.31 at episode 888860
running reward: 19.83 at episode 888870
running reward: 20.65 at episode 888880
running reward: 19.57 at episode 888890
running reward: 19.56 at episode 888900
running reward: 17.11 at episode 888910
running reward: 18.63 at episode 888920
running reward: 17.79 at episode 888930
running reward: 18.59 at episode 888940
running reward: 19.42 at episode 888950


ResourceExhaustedError: OOM when allocating tensor with shape[1,256] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc [Op:BiasAdd]